# Capstone Project
## Problem : Where would be recommended if someone want to open a restaurant in Queens ?

### Introduction
The data will be get from the New York Geojson, and the Foursquare map. The data will contain only the 'food' categories and the distance to Flushing Main Street which represent traffic convenience. With these data, we can get the information of food shop density and traffic convenience. Then, with clustering analysis, we can know that neighborhood has similar characteristic.

### Data

Base on our problem, some features we want to get are: <br>
* Every restaurant or food related shop in Queens
* The categories composition of each neighborhood
* The average distance to Flushing Main Street of every venues in each neighborhood

Data source are following: <br>
* Explore food related shop or restaurant in specific region by Foursquare API
* With the latitude and longitude information, the distance from each venue to Flushing Main Street could be calculated

### Methodology
* In the first step, we get the longitude and latitude of Flushing Main Street by Foursquare API. Then we use the Geojson data in this course to get the neighborhood information in Queens. <br>
* Second step we use Foursquare API and information in last step to get the venues list in each neighborhood. Then the venues are filtered with categories such as food shop or restaurant. <br>
* In third step, the distance from each venue to Flushing Main Street train station is calculated by longitude and latitude. These information represent the traffic convinence of each venue. <br>
* In final step, we use one hot encoding to transform category data to value, and combine the data to distance data, then use different method to cluster every neighborhood.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /Users/steventsai/opt/anaconda3

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    archspec-0.1.1             |     pyh9f0ad1d_0          25 KB  conda-forge
    conda-4.8.4                |   py37hc8dfbb8_1         3.0 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.0 MB

The following NEW packages will be INSTALLED:

  archspec           conda-forge/noarch::archspec-0.1.1-pyh9f0ad1d_0

The following packages will be UPDATED:

  conda                                4.8.3-py37hc8dfbb8_1 --> 4.8.4-py37hc8dfbb8_1



conda-4.8.4          | 3.0 MB    | ##################################### | 100% 
archspec-0.1.1       | 25 KB     | ##################################### | 100% 
Preparing transact

## Using the New York Geojson data

In [2]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
neighborhoods_data = newyork_data['features']

# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

## Get the latitude and longitude of Flushing Main Street

In [3]:
address = 'Flushing Main Street'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of NY are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of NY are 40.7585195, -73.8298574.


In [4]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [5]:
print(neighborhoods.shape)
neighborhoods.head()

(306, 4)


Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

## Get the data of Queens

In [6]:
queen_data = neighborhoods[neighborhoods['Borough'] == 'Queens'].reset_index(drop=True)
print(queen_data.shape)
queen_data.head()

(81, 4)


Borough     Neighborhood   Latitude  Longitude
0  Queens          Astoria  40.768509 -73.915654
1  Queens         Woodside  40.746349 -73.901842
2  Queens  Jackson Heights  40.751981 -73.882821
3  Queens         Elmhurst  40.744049 -73.881656
4  Queens     Howard Beach  40.654225 -73.838138

In [7]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [8]:
CLIENT_ID = 'OA0DRW3PDAHDZFVOP4IXML5MMCNNMWQHBBU1ERAP1CTCIZLD' # your Foursquare ID
CLIENT_SECRET = '2F3HF1ZFTNCLO1F5IN2ZFILSZQQDXSNJROIOVB2R5IM2S0A3' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: OA0DRW3PDAHDZFVOP4IXML5MMCNNMWQHBBU1ERAP1CTCIZLD
CLIENT_SECRET:2F3HF1ZFTNCLO1F5IN2ZFILSZQQDXSNJROIOVB2R5IM2S0A3


In [9]:
cat = '4d4b7105d754a06374d81259'
LIMIT = 200
radius = 10000
sortP = 1
sec = 'food'

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}&sortByPopularity={}&section={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
    longitude,
    radius,
    LIMIT,
    cat,
    sortP,
    sec)

results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f30fcdc2cc28e57cedd2c4e'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': '$-$$$$', 'key': 'price'}]},
  'headerLocation': 'Queens',
  'headerFullLocation': 'Queens',
  'headerLocationGranularity': 'city',
  'query': 'food',
  'totalResults': 250,
  'suggestedBounds': {'ne': {'lat': 40.84851959000009,
    'lng': -73.71126221232828},
   'sw': {'lat': 40.66851940999991, 'lng': -73.94845258767171}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b3ea6eaf964a52058a025e3',
       'name': 'Peter Luger Steak House',
       'location': {'address': '225 Northern Blvd',
        'crossStreet': 'btwn Tain Dr & Merrivale Rd',
        'lat': 40.777245373268975,
   

In [10]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/Users/steventsai/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name            categories        lat        lng
0      Peter Luger Steak House            Steakhouse  40.777245 -73.727541
1                   Mexicocina    Mexican Restaurant  40.811837 -73.909512
2           Trinciti Roti Shop  Caribbean Restaurant  40.680314 -73.821202
3  Patsy's Pizza - East Harlem           Pizza Place  40.797108 -73.934626
4     You Garden Xiao Long Bao   Shanghai Restaurant  40.763364 -73.770664

In [11]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


In [12]:
distance = venues[0]['venue']['location']['distance']
type(distance)

int

In [13]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        cat = '4d4b7105d754a06374d81259'
        LIMIT = 200
        sortP = 1
        sec = 'food'
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}&sortByPopularity={}&section={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT,
            cat,
            sortP,
            sec)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'], 
            v['venue']['location']['distance'],
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue distance',
                  'Venue Category']
    
    return(nearby_venues)

In [14]:
Q_venues = getNearbyVenues(names=queen_data['Neighborhood'],
                                   latitudes=queen_data['Latitude'],
                                   longitudes=queen_data['Longitude']
                                  )

Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
Corona
Forest Hills
Kew Gardens
Richmond Hill
Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Rego Park
Woodhaven
Ozone Park
South Ozone Park
College Point
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Hollis
South Jamaica
St. Albans
Rochdale
Springfield Gardens
Cambria Heights
Rosedale
Far Rockaway
Broad Channel
Breezy Point
Steinway
Beechhurst
Bay Terrace
Edgemere
Arverne
Rockaway Beach
Neponsit
Murray Hill
Floral Park
Holliswood
Jamaica Estates
Queensboro Hill
Hillcrest
Ravenswood
Lindenwood
Laurelton
Lefrak City
Belle Harbor
Rockaway Park
Somerville
Brookville
Bellaire
North Corona
Forest Hills Gardens
Jamaica Hills
Utopia
Pomonok
Astoria Heights
Hunters Point
Sunnyside Gardens
Blissville
Roxbury
Middle Village
Malba
Hammels
Bayswater
Queensbridge


In [15]:
print(Q_venues.shape)
Q_venues.head()

(1610, 8)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

                                Venue  Venue Latitude  Venue Longitude  \
0                       Neptune Diner       40.770788       -73.916890   
1                         Sugar Freak       40.764443       -73.916055   
2  New York City Bagel & Coffee House       40.765841       -73.919441   
3         Brooklyn Bagel & Coffee Co.       40.764732       -73.916944   
4                       George's Deli       40.766316       -73.915284   

   Venue distance             Venue Category  
0             274                      Diner  
1             453  Cajun / Creole Restaurant  
2             436                 Bagel Shop  
3             434                 Bagel Shop  
4             246              Deli / Bodega

In [16]:
Q_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Arverne                                   8                       8      8   
Astoria                                  89                      89     89   
Astoria Heights                           9                       9      9   
Auburndale                               10                      10     10   
Bay Terrace                              11                      11     11   
Bayside                                  59                      59     59   
Beechhurst                                7                       7      7   
Bellaire                                  8                       8      8   
Belle Harbor                              8                       8      8   
Bellerose                                16                      16     16   
Blissville                               13                      13     13   
Briarwood                                 5                       5      5   
Broad Channel                             5                       5      5   
Brookville                                2                       2      2   
Cambria Heights                           9                       9      9   
College Point                            45                      45     45   
Corona                                   21                      21     21   
Douglaston                               23                      23     23   
East Elmhurst                            11                      11     11   
Edgemere                                  4                       4      4   
Elmhurst                                 25                      25     25   
Far Rockaway                             24                      24     24   
Floral Park                               7                       7      7   
Flushing                                 67                      67     67   
Forest Hills                             25                      25     25   
Forest Hills Gardens                     19                      19     19   
Fresh Meadows                             5                       5      5   
Glen Oaks                                11                      11     11   
Glendale                                  7                       7      7   
Hammels                                   5                       5      5   
Hillcrest                                16                      16     16   
Hollis                                    5                       5      5   
Holliswood                                3                       3      3   
Howard Beach                             24                      24     24   
Hunters Point                            45                      45     45   
Jackson Heights                          61                      61     61   
Jamaica Center                           28                      28     28   
Jamaica Estates                           1                       1      1   
Jamaica Hills                            29                      29     29   
Kew Gardens                              30                      30     30   
Kew Gardens Hills                        15                      15     15   
Laurelton                                 4                       4      4   
Lefrak City                              21                      21     21   
Lindenwood                                7                       7      7   
Little Neck                              42                      42     42   
Long Island City                         44                      44     44   
Malba                                     1                       1      1   
Maspeth                                  26                      26     26   
Middle Village                           15                      15     15   
Murray Hill                              40 

In [17]:
print('There are {} unique categories.'.format(len(Q_venues['Venue Category'].unique())))

There are 98 unique categories.


In [18]:
# one hot encoding
Q_onehot = pd.get_dummies(Q_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Q_onehot['Neighborhood'] = Q_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Q_onehot.columns[-1]] + list(Q_onehot.columns[:-1])
Q_onehot = Q_onehot[fixed_columns]

Q_onehot.head()

Neighborhood  Afghan Restaurant  American Restaurant  Arepa Restaurant  \
0      Astoria                  0                    0                 0   
1      Astoria                  0                    0                 0   
2      Astoria                  0                    0                 0   
3      Astoria                  0                    0                 0   
4      Astoria                  0                    0                 0   

   Argentinian Restaurant  Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                       0                 0          0           0       0   
1                       0                 0          0           0       0   
2                       0                 0          0           1       0   
3                       0                 0          0           1       0   
4                       0                 0          0           0       0   

   Bistro  Brazilian Restaurant  Breakfast Spot  Buffet  Burger Joint  \
0       0                     0               0       0             0   
1       0                     0               0       0             0   
2       0                     0               0       0             0   
3       0                     0               0       0             0   
4       0                     0               0       0             0   

   Burrito Place  Cafeteria  Café  Cajun / Creole Restaurant  \
0              0          0     0                          0   
1              0          0     0                          1   
2              0          0     0                          0   
3              0          0     0                          0   
4              0          0     0                          0   

   Cantonese Restaurant  Caribbean Restaurant  Chinese Restaurant  \
0                     0                     0                   0   
1                     0                     0                   0   
2                     0                     0                   0   
3                     0                     0                   0   
4                     0                     0                   0   

   Colombian Restaurant  Comfort Food Restaurant  Cuban Restaurant  \
0                     0                        0                 0   
1                     0                        0                 0   
2                     0                        0                 0   
3                     0                        0                 0   
4                     0                        0                 0   

   Deli / Bodega  Dim Sum Restaurant  Diner  Donut Shop  Dosa Place  \
0              0                   0      1           0           0   
1              0                   0      0           0           0   
2              0                   0      0           0           0   
3              0                   0      0           0           0   
4              1                   0      0           0           0   

   Dumpling Restaurant  Eastern European Restaurant  Egyptian Restaurant  \
0                    0                            0                    0   
1                    0                            0                    0   
2                    0                            0                    0   
3                    0                            0                    0   
4                    0                            0                    0   

   Empanada Restaurant  Falafel Restaurant  Fast Food Restaurant  \
0                    0                   0                     0   
1                    0                   0                     0   
2                    0                   0                     0   
3                    0                   0                     0   
4                    0                   0                     0   

   Filipino Restaurant  Fish & Chips Shop  Food  Food Court  Food Stand  \
0                    0                  0     0 

In [19]:
Q_onehot.shape

(1610, 99)

In [20]:
Q_grouped = Q_onehot.groupby('Neighborhood').mean().reset_index()
Q_grouped

Neighborhood  Afghan Restaurant  American Restaurant  \
0                Arverne           0.000000             0.000000   
1                Astoria           0.000000             0.011236   
2        Astoria Heights           0.000000             0.000000   
3             Auburndale           0.000000             0.100000   
4            Bay Terrace           0.000000             0.181818   
5                Bayside           0.000000             0.050847   
6             Beechhurst           0.000000             0.000000   
7               Bellaire           0.000000             0.000000   
8           Belle Harbor           0.000000             0.000000   
9              Bellerose           0.000000             0.062500   
10            Blissville           0.000000             0.000000   
11             Briarwood           0.000000             0.000000   
12         Broad Channel           0.000000             0.000000   
13            Brookville           0.000000             0.000000   
14       Cambria Heights           0.000000             0.000000   
15         College Point           0.000000             0.000000   
16                Corona           0.000000             0.000000   
17            Douglaston           0.000000             0.000000   
18         East Elmhurst           0.000000             0.090909   
19              Edgemere           0.000000             0.000000   
20              Elmhurst           0.000000             0.000000   
21          Far Rockaway           0.000000             0.000000   
22           Floral Park           0.000000             0.000000   
23              Flushing           0.000000             0.000000   
24          Forest Hills           0.000000             0.000000   
25  Forest Hills Gardens           0.000000             0.000000   
26         Fresh Meadows           0.000000             0.000000   
27             Glen Oaks           0.000000             0.000000   
28              Glendale           0.000000             0.000000   
29               Hammels           0.000000             0.000000   
30             Hillcrest           0.000000             0.000000   
31                Hollis           0.000000             0.000000   
32            Holliswood           0.000000             0.000000   
33          Howard Beach           0.000000             0.000000   
34         Hunters Point           0.000000             0.044444   
35       Jackson Heights           0.000000             0.000000   
36        Jamaica Center           0.000000             0.071429   
37       Jamaica Estates           0.000000             0.000000   
38         Jamaica Hills           0.000000             0.000000   
39           Kew Gardens           0.000000             0.033333   
40     Kew Gardens Hills           0.000000             0.000000   
41             Laurelton           0.000000             0.000000   
42           Lefrak City           0.000000             0.000000   
43            Lindenwood           0.000000             0.000000   
44           Little Neck           0.000000             0.000000   
45      Long Island City           0.000000             0.022727   
46                 Malba           0.000000             0.000000   
47               Maspeth           0.000000             0.000000   
48        Middle Village           0.000000             0.000000   
49           Murray Hill           0.000000             0.000000   
50          North Corona           0.000000             0.000000   
51       Oakland Gardens           0.000000             0.000000   
52            Ozone Park           0.000000             0.000000   
53               Pomonok           0.000000             0.200000   
54        Queens Village           0.000000             0.000000   
55       Queensboro Hill           0.000000             0.000000   
56          Queensbridge           0.000000             0.000000   
57            Ravenswood           0.026316             0.000000   


In [21]:
Q_grouped.shape

(77, 99)

In [22]:
num_top_venues = 5

for hood in Q_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = Q_grouped[Q_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Arverne----
             venue  freq
0   Sandwich Place  0.25
1       Restaurant  0.12
2             Café  0.12
3       Donut Shop  0.12
4  Thai Restaurant  0.12


----Astoria----
                       venue  freq
0  Middle Eastern Restaurant  0.10
1              Deli / Bodega  0.08
2           Greek Restaurant  0.07
3          Indian Restaurant  0.07
4                     Bakery  0.07


----Astoria Heights----
                venue  freq
0  Italian Restaurant  0.22
1  Chinese Restaurant  0.22
2       Deli / Bodega  0.11
3         Pizza Place  0.11
4              Bakery  0.11


----Auburndale----
                  venue  freq
0    Italian Restaurant   0.3
1                 Diner   0.1
2     Korean Restaurant   0.1
3  Fast Food Restaurant   0.1
4          Noodle House   0.1


----Bay Terrace----
                 venue  freq
0           Donut Shop  0.18
1  American Restaurant  0.18
2          Pizza Place  0.18
3               Bakery  0.09
4          Salad Place  0.09


----Bayside--

                venue  freq
0       Deli / Bodega  0.15
1         Pizza Place  0.12
2               Diner  0.12
3  Chinese Restaurant  0.12
4              Bakery  0.08


----Middle Village----
                venue  freq
0  Chinese Restaurant  0.20
1              Bakery  0.13
2  Spanish Restaurant  0.07
3       Burrito Place  0.07
4    Sushi Restaurant  0.07


----Murray Hill----
                 venue  freq
0    Korean Restaurant  0.70
1        Deli / Bodega  0.05
2          Pizza Place  0.02
3           Restaurant  0.02
4  Fried Chicken Joint  0.02


----North Corona----
                venue  freq
0       Deli / Bodega  0.22
1         Pizza Place  0.17
2              Bakery  0.17
3  Mexican Restaurant  0.11
4  Spanish Restaurant  0.06


----Oakland Gardens----
                venue  freq
0   Korean Restaurant  0.29
1  Chinese Restaurant  0.18
2          Donut Shop  0.07
3       Deli / Bodega  0.07
4    Sushi Restaurant  0.04


----Ozone Park----
                       venue  freq
0 

In [23]:
Q_venues.groupby([ 'Neighborhood', 'Venue Category']).mean()

Neighborhood Latitude  \
Neighborhood         Venue Category                                           
Arverne              Burrito Place                                40.589144   
                     Café                                         40.589144   
                     Donut Shop                                   40.589144   
                     Pizza Place                                  40.589144   
                     Restaurant                                   40.589144   
                     Sandwich Place                               40.589144   
                     Thai Restaurant                              40.589144   
Astoria              American Restaurant                          40.768509   
                     BBQ Joint                                    40.768509   
                     Bagel Shop                                   40.768509   
                     Bakery                                       40.768509   
                     Brazilian Restaurant                         40.768509   
                     Breakfast Spot                               40.768509   
                     Burger Joint                                 40.768509   
                     Café                                         40.768509   
                     Cajun / Creole Restaurant                    40.768509   
                     Chinese Restaurant                           40.768509   
                     Comfort Food Restaurant                      40.768509   
                     Deli / Bodega                                40.768509   
                     Diner                                        40.768509   
                     Falafel Restaurant                           40.768509   
                     Fast Food Restaurant                         40.768509   
                     Food                                         40.768509   
                     Food Truck                                   40.768509   
                     Greek Restaurant                             40.768509   
                     Halal Restaurant                             40.768509   
                     Indian Restaurant                            40.768509   
                     Irish Pub                                    40.768509   
                     Italian Restaurant                           40.768509   
                     Japanese Restaurant                          40.768509   
                     Korean Restaurant                            40.768509   
                     Latin American Restaurant                    40.768509   
                     Mediterranean Restaurant                     40.768509   
                     Mexican Restaurant                           40.768509   
                     Middle Eastern Restaurant                    40.768509   
                     Moroccan Restaurant                          40.768509   
                     New American Restaurant                      40.768509   
                     Pizza Place                                  40.768509   
                     Poke Place                                   40.768509   
                     Restaurant                                   40.768509   
                     Sandwich Place                               40.768509   
                     Seafood Restaurant                           40.768509   
                     Souvlaki Shop                                40.768509   
                     Sushi Restaurant                             40.768509   
                     Thai Restaurant                              40.768509   
                     Vegetarian / Vegan Restaurant                40.768509   
Astoria Heights      Bakery                                       40.770317   
                     Burger Joint                                 40.770317   
                     Chinese Restaurant                           40.770317   
                     Deli

## Define a function of calculating the distance of each venue to Flushing Main Street by longitude and latitude

In [24]:
import math
def distance_cal(lat1,lon1,lat2,lon2):
    R = 6137e3
    phi1 = lat1 * math.pi/180
    phi2 = lat2 * math.pi/180
    dphi = (lat2-lat1) * math.pi/180
    dlam = (lon2-lon1) * math.pi/180
    a = math.sin(dphi/2) * math.sin(dphi/2) + math.cos(phi1) * math.cos(phi2) * math.sin(dlam/2) * math.sin(dlam/2)
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a))
    d = R * c
    return d

In [25]:
# Flushin Main Street latitude and longitude
lat1 = 40.7585195
lon1 = -73.8298574
# Calculate the distance to Flushing Main Street of each venue
dist_to_Flushing = []
for name, lat2, lon2 in zip(Q_venues['Venue'], Q_venues['Venue Latitude'], Q_venues['Venue Longitude']):
    d = distance_cal(lat1, lon1, lat2, lon2)
    dist_to_Flushing.append([name, int(d)])

dist_df = pd.DataFrame(dist_to_Flushing)
dist_df.rename(columns = {0:'Venue', 1:'Distance'}, inplace = True)

In [26]:
print(dist_df.shape)
dist_df

(1610, 2)


Venue  Distance
0                                         Neptune Diner      7181
1                                           Sugar Freak      7021
2                    New York City Bagel & Coffee House      7309
3                           Brooklyn Bagel & Coffee Co.      7096
4                                         George's Deli      6980
5                                      Zyara Restaurant      6777
6                                           Butcher Bar      7039
7                                             The Grand      7056
8                               Koroni Souvlaki & Grill      7485
9                                        Queens Comfort      7082
10                          Al-sham Sweets and Pastries      6706
11                        Leli's Bakery and Pastry Shop      7161
12                                     Nonna’s Pizzeria      6585
13                                          Burger Club      7409
14                                               Mombar      6746
15                                        Blend Astoria      6997
16                                      Sissy McGinty's      6796
17                                 Ovelia Psistaria Bar      7264
18                                 New York Bakery Café      7389
19                                  Café To Go Creperie      7402
20                               Basil Brick Oven Pizza      7437
21                                            The Gully      6754
22                                              Sabry's      6689
23                                       AbuQir Seafood      6683
24                                Farid Kebab, Steinway      6731
25                                             Gyro Uno      6839
26                                     Mochiron Izakaya      7229
27                                           Gyro World      7132
28                                              SVL Bar      7294
29                            Dave and Tony's Salumeria      7218
30                                   Grand Avenue Pizza      7206
31                                 Pochana Thai Kitchen      7295
32                                           Via Trenta      7072
33                                           Kabab Café      6728
34                                Elias Corner For Fish      7132
35                                  Seva Indian Cuisine      7283
36                                       Little Morocco      6703
37                                         Off The Hook      7219
38                                            Pink Nori      7120
39                                        Crave Astoria      7120
40                                         Poke Burrito      7039
41                                        Astoria Pizza      7396
42                            International Meat Market      7102
43                                                Duzan      6674
44                      Golden House Chinese Restaurant      7167
45                                          Jujube Tree      7200
46                                         Layali Dubai      6666
47                                         Favela Grill      7204
48                                            Viva Viva      7251
49                                        Kurry Qulture      7115
50                                               Sampan      6908
51                                                  Kal      7249
52                         Antika Restaurant & Pizzeria      7115
53                                   Tikka Indian Grill      7241
54                                             Pita Pan      7014
55                                    Café Via Espresso      6660
56                                         AwesomeSauce      6643
57                                            Azal Food      6714
58                                       Golden Kitchen      7344
59                                       Hangar Astoria      6877
60                      

In [27]:
Q_venues_d = pd.concat([Q_venues, dist_df['Distance']], axis = 1)
Q_venues_d.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

                                Venue  Venue Latitude  Venue Longitude  \
0                       Neptune Diner       40.770788       -73.916890   
1                         Sugar Freak       40.764443       -73.916055   
2  New York City Bagel & Coffee House       40.765841       -73.919441   
3         Brooklyn Bagel & Coffee Co.       40.764732       -73.916944   
4                       George's Deli       40.766316       -73.915284   

   Venue distance             Venue Category  Distance  
0             274                      Diner      7181  
1             453  Cajun / Creole Restaurant      7021  
2             436                 Bagel Shop      7309  
3             434                 Bagel Shop      7096  
4             246              Deli / Bodega      6980

In [28]:
Q_venues_d.drop(['Venue distance'], axis = 1, inplace = True)

In [29]:
Q_venues_d

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                  Astoria              40.768509              -73.915654   
1                  Astoria              40.768509              -73.915654   
2                  Astoria              40.768509              -73.915654   
3                  Astoria              40.768509              -73.915654   
4                  Astoria              40.768509              -73.915654   
5                  Astoria              40.768509              -73.915654   
6                  Astoria              40.768509              -73.915654   
7                  Astoria              40.768509              -73.915654   
8                  Astoria              40.768509              -73.915654   
9                  Astoria              40.768509              -73.915654   
10                 Astoria              40.768509              -73.915654   
11                 Astoria              40.768509              -73.915654   
12                 Astoria              40.768509              -73.915654   
13                 Astoria              40.768509              -73.915654   
14                 Astoria              40.768509              -73.915654   
15                 Astoria              40.768509              -73.915654   
16                 Astoria              40.768509              -73.915654   
17                 Astoria              40.768509              -73.915654   
18                 Astoria              40.768509              -73.915654   
19                 Astoria              40.768509              -73.915654   
20                 Astoria              40.768509              -73.915654   
21                 Astoria              40.768509              -73.915654   
22                 Astoria              40.768509              -73.915654   
23                 Astoria              40.768509              -73.915654   
24                 Astoria              40.768509              -73.915654   
25                 Astoria              40.768509              -73.915654   
26                 Astoria              40.768509              -73.915654   
27                 Astoria              40.768509              -73.915654   
28                 Astoria              40.768509              -73.915654   
29                 Astoria              40.768509              -73.915654   
30                 Astoria              40.768509              -73.915654   
31                 Astoria              40.768509              -73.915654   
32                 Astoria              40.768509              -73.915654   
33                 Astoria              40.768509              -73.915654   
34                 Astoria              40.768509              -73.915654   
35                 Astoria              40.768509              -73.915654   
36                 Astoria              40.768509              -73.915654   
37                 Astoria              40.768509              -73.915654   
38                 Astoria              40.768509              -73.915654   
39                 Astoria              40.768509              -73.915654   
40                 Astoria              40.768509              -73.915654   
41                 Astoria              40.768509              -73.915654   
42                 Astoria              40.768509              -73.915654   
43                 Astoria              40.768509              -73.915654   
44                 Astoria              40.768509              -73.915654   
45                 Astoria              40.768509              -73.915654   
46                 Astoria              40.768509              -73.915654   
47                 Astoria              40.768509              -73.915654   
48                 Astoria              40.768509              -73.915654   
49                 Astoria              40.768509              -73.915654   
50                 Astoria              40.768509              -73.915654   
51        

## Get the average distance of all venues in the neighborhood

In [99]:
Q_distance_M = Q_venues_d.groupby('Neighborhood').mean()
Q_distance_M

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                          
Arverne                           40.589144              -73.791992   
Astoria                           40.768509              -73.915654   
Astoria Heights                   40.770317              -73.894680   
Auburndale                        40.761730              -73.791762   
Bay Terrace                       40.782843              -73.776802   
Bayside                           40.766041              -73.774274   
Beechhurst                        40.792781              -73.804365   
Bellaire                          40.733014              -73.738892   
Belle Harbor                      40.576156              -73.854018   
Bellerose                         40.728573              -73.720128   
Blissville                        40.737251              -73.932442   
Briarwood                         40.710935              -73.811748   
Broad Channel                     40.603027              -73.820055   
Brookville                        40.660003              -73.751753   
Cambria Heights                   40.692775              -73.735269   
College Point                     40.784903              -73.843045   
Corona                            40.742382              -73.856825   
Douglaston                        40.766846              -73.742498   
East Elmhurst                     40.764073              -73.867041   
Edgemere                          40.595642              -73.776133   
Elmhurst                          40.744049              -73.881656   
Far Rockaway                      40.603134              -73.754980   
Floral Park                       40.741378              -73.708847   
Flushing                          40.764454              -73.831773   
Forest Hills                      40.725264              -73.844475   
Forest Hills Gardens              40.714611              -73.841022   
Fresh Meadows                     40.734394              -73.782713   
Glen Oaks                         40.749441              -73.715481   
Glendale                          40.702762              -73.870742   
Hammels                           40.587338              -73.805530   
Hillcrest                         40.723825              -73.797603   
Hollis                            40.711243              -73.759250   
Holliswood                        40.720957              -73.767142   
Howard Beach                      40.654225              -73.838138   
Hunters Point                     40.743414              -73.953868   
Jackson Heights                   40.751981              -73.882821   
Jamaica Center                    40.704657              -73.796902   
Jamaica Estates                   40.716805              -73.787227   
Jamaica Hills                     40.711460              -73.796465   
Kew Gardens                       40.705179              -73.829819   
Kew Gardens Hills                 40.722578              -73.820878   
Laurelton                         40.667884              -73.740256   
Lefrak City                       40.736075              -73.862525   
Lindenwood                        40.663918              -73.849638   
Little Neck                       40.770826              -73.738898   
Long Island City                  40.750217              -73.939202   
Malba                             40.790602              -73.826678   
Maspeth                           40.725427              -73.896217   
Middle Village                    40.716415              -73.881143   
Murray Hill                       40.764126              -73.812763   
North Corona                      40.754071              -73.857518   
Oakland Gardens                   40.745619              -73.754950   
Ozone Park                        40.680708              -73.843203   
Pomonok                           40.734936              -73.804861   
Queens Village                    40.718893   

## Transfer dataframe by one hot encoding 

In [31]:
# one hot encoding
Q_onehot = pd.get_dummies(Q_venues_d[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Q_onehot['Neighborhood'] = Q_venues_d['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Q_onehot.columns[-1]] + list(Q_onehot.columns[:-1])
Q_onehot = Q_onehot[fixed_columns]

Q_onehot.head()

Neighborhood  Afghan Restaurant  American Restaurant  Arepa Restaurant  \
0      Astoria                  0                    0                 0   
1      Astoria                  0                    0                 0   
2      Astoria                  0                    0                 0   
3      Astoria                  0                    0                 0   
4      Astoria                  0                    0                 0   

   Argentinian Restaurant  Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                       0                 0          0           0       0   
1                       0                 0          0           0       0   
2                       0                 0          0           1       0   
3                       0                 0          0           1       0   
4                       0                 0          0           0       0   

   Bistro  Brazilian Restaurant  Breakfast Spot  Buffet  Burger Joint  \
0       0                     0               0       0             0   
1       0                     0               0       0             0   
2       0                     0               0       0             0   
3       0                     0               0       0             0   
4       0                     0               0       0             0   

   Burrito Place  Cafeteria  Café  Cajun / Creole Restaurant  \
0              0          0     0                          0   
1              0          0     0                          1   
2              0          0     0                          0   
3              0          0     0                          0   
4              0          0     0                          0   

   Cantonese Restaurant  Caribbean Restaurant  Chinese Restaurant  \
0                     0                     0                   0   
1                     0                     0                   0   
2                     0                     0                   0   
3                     0                     0                   0   
4                     0                     0                   0   

   Colombian Restaurant  Comfort Food Restaurant  Cuban Restaurant  \
0                     0                        0                 0   
1                     0                        0                 0   
2                     0                        0                 0   
3                     0                        0                 0   
4                     0                        0                 0   

   Deli / Bodega  Dim Sum Restaurant  Diner  Donut Shop  Dosa Place  \
0              0                   0      1           0           0   
1              0                   0      0           0           0   
2              0                   0      0           0           0   
3              0                   0      0           0           0   
4              1                   0      0           0           0   

   Dumpling Restaurant  Eastern European Restaurant  Egyptian Restaurant  \
0                    0                            0                    0   
1                    0                            0                    0   
2                    0                            0                    0   
3                    0                            0                    0   
4                    0                            0                    0   

   Empanada Restaurant  Falafel Restaurant  Fast Food Restaurant  \
0                    0                   0                     0   
1                    0                   0                     0   
2                    0                   0                     0   
3                    0                   0                     0   
4                    0                   0                     0   

   Filipino Restaurant  Fish & Chips Shop  Food  Food Court  Food Stand  \
0                    0                  0     0 

In [32]:
Q_grouped = Q_onehot.groupby('Neighborhood').mean().reset_index()
Q_grouped.sort_values(by='Neighborhood',inplace = True)
Q_grouped

Neighborhood  Afghan Restaurant  American Restaurant  \
0                Arverne           0.000000             0.000000   
1                Astoria           0.000000             0.011236   
2        Astoria Heights           0.000000             0.000000   
3             Auburndale           0.000000             0.100000   
4            Bay Terrace           0.000000             0.181818   
5                Bayside           0.000000             0.050847   
6             Beechhurst           0.000000             0.000000   
7               Bellaire           0.000000             0.000000   
8           Belle Harbor           0.000000             0.000000   
9              Bellerose           0.000000             0.062500   
10            Blissville           0.000000             0.000000   
11             Briarwood           0.000000             0.000000   
12         Broad Channel           0.000000             0.000000   
13            Brookville           0.000000             0.000000   
14       Cambria Heights           0.000000             0.000000   
15         College Point           0.000000             0.000000   
16                Corona           0.000000             0.000000   
17            Douglaston           0.000000             0.000000   
18         East Elmhurst           0.000000             0.090909   
19              Edgemere           0.000000             0.000000   
20              Elmhurst           0.000000             0.000000   
21          Far Rockaway           0.000000             0.000000   
22           Floral Park           0.000000             0.000000   
23              Flushing           0.000000             0.000000   
24          Forest Hills           0.000000             0.000000   
25  Forest Hills Gardens           0.000000             0.000000   
26         Fresh Meadows           0.000000             0.000000   
27             Glen Oaks           0.000000             0.000000   
28              Glendale           0.000000             0.000000   
29               Hammels           0.000000             0.000000   
30             Hillcrest           0.000000             0.000000   
31                Hollis           0.000000             0.000000   
32            Holliswood           0.000000             0.000000   
33          Howard Beach           0.000000             0.000000   
34         Hunters Point           0.000000             0.044444   
35       Jackson Heights           0.000000             0.000000   
36        Jamaica Center           0.000000             0.071429   
37       Jamaica Estates           0.000000             0.000000   
38         Jamaica Hills           0.000000             0.000000   
39           Kew Gardens           0.000000             0.033333   
40     Kew Gardens Hills           0.000000             0.000000   
41             Laurelton           0.000000             0.000000   
42           Lefrak City           0.000000             0.000000   
43            Lindenwood           0.000000             0.000000   
44           Little Neck           0.000000             0.000000   
45      Long Island City           0.000000             0.022727   
46                 Malba           0.000000             0.000000   
47               Maspeth           0.000000             0.000000   
48        Middle Village           0.000000             0.000000   
49           Murray Hill           0.000000             0.000000   
50          North Corona           0.000000             0.000000   
51       Oakland Gardens           0.000000             0.000000   
52            Ozone Park           0.000000             0.000000   
53               Pomonok           0.000000             0.200000   
54        Queens Village           0.000000             0.000000   
55       Queensboro Hill           0.000000             0.000000   
56          Queensbridge           0.000000             0.000000   
57            Ravenswood           0.026316             0.000000   


In [33]:
Q_mergeD = Q_grouped.merge(Q_distance_M, on = 'Neighborhood')

In [37]:
Q_mergeD.drop(columns=['Neighborhood Latitude', 'Neighborhood Longitude', 'Venue Latitude', 'Venue Longitude',], axis = 1, inplace = True)

In [38]:
Q_mergeD

Neighborhood  Afghan Restaurant  American Restaurant  \
0                Arverne           0.000000             0.000000   
1                Astoria           0.000000             0.011236   
2        Astoria Heights           0.000000             0.000000   
3             Auburndale           0.000000             0.100000   
4            Bay Terrace           0.000000             0.181818   
5                Bayside           0.000000             0.050847   
6             Beechhurst           0.000000             0.000000   
7               Bellaire           0.000000             0.000000   
8           Belle Harbor           0.000000             0.000000   
9              Bellerose           0.000000             0.062500   
10            Blissville           0.000000             0.000000   
11             Briarwood           0.000000             0.000000   
12         Broad Channel           0.000000             0.000000   
13            Brookville           0.000000             0.000000   
14       Cambria Heights           0.000000             0.000000   
15         College Point           0.000000             0.000000   
16                Corona           0.000000             0.000000   
17            Douglaston           0.000000             0.000000   
18         East Elmhurst           0.000000             0.090909   
19              Edgemere           0.000000             0.000000   
20              Elmhurst           0.000000             0.000000   
21          Far Rockaway           0.000000             0.000000   
22           Floral Park           0.000000             0.000000   
23              Flushing           0.000000             0.000000   
24          Forest Hills           0.000000             0.000000   
25  Forest Hills Gardens           0.000000             0.000000   
26         Fresh Meadows           0.000000             0.000000   
27             Glen Oaks           0.000000             0.000000   
28              Glendale           0.000000             0.000000   
29               Hammels           0.000000             0.000000   
30             Hillcrest           0.000000             0.000000   
31                Hollis           0.000000             0.000000   
32            Holliswood           0.000000             0.000000   
33          Howard Beach           0.000000             0.000000   
34         Hunters Point           0.000000             0.044444   
35       Jackson Heights           0.000000             0.000000   
36        Jamaica Center           0.000000             0.071429   
37       Jamaica Estates           0.000000             0.000000   
38         Jamaica Hills           0.000000             0.000000   
39           Kew Gardens           0.000000             0.033333   
40     Kew Gardens Hills           0.000000             0.000000   
41             Laurelton           0.000000             0.000000   
42           Lefrak City           0.000000             0.000000   
43            Lindenwood           0.000000             0.000000   
44           Little Neck           0.000000             0.000000   
45      Long Island City           0.000000             0.022727   
46                 Malba           0.000000             0.000000   
47               Maspeth           0.000000             0.000000   
48        Middle Village           0.000000             0.000000   
49           Murray Hill           0.000000             0.000000   
50          North Corona           0.000000             0.000000   
51       Oakland Gardens           0.000000             0.000000   
52            Ozone Park           0.000000             0.000000   
53               Pomonok           0.000000             0.200000   
54        Queens Village           0.000000             0.000000   
55       Queensboro Hill           0.000000             0.000000   
56          Queensbridge           0.000000             0.000000   
57            Ravenswood           0.026316             0.000000   


In [43]:
from sklearn.cluster import KMeans, DBSCAN
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler

In [98]:
X = Q_mergeD.values[:,1:]
kclusters = 10
clus_Kdata = StandardScaler().fit_transform(X)
k_means = KMeans(init = "k-means++", n_clusters = kclusters, n_init = 100)
k_means.fit(X)
K_labels = k_means.labels_
K_labels

array([2, 1, 6, 8, 3, 3, 3, 7, 9, 4, 7, 6, 2, 5, 4, 8, 8, 1, 8, 2, 3, 2,
       4, 0, 3, 3, 3, 4, 1, 2, 3, 1, 1, 5, 4, 3, 6, 6, 6, 6, 3, 5, 3, 4,
       1, 7, 8, 6, 6, 0, 8, 6, 7, 8, 7, 0, 7, 7, 3, 6, 1, 4, 2, 9, 5, 9,
       1, 4, 5, 7, 6, 1, 1, 3, 8, 1, 6], dtype=int32)

In [100]:
# add clustering labels
Q_distance_M.insert(0, 'Cluster Labels', K_labels)
Q_distance_M
##manhattan_merged = manhattan_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
##Q_mergeC = Q_distance_M.join(Q_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

##Q_mergeC.head() # check the last columns!

Cluster Labels  Neighborhood Latitude  \
Neighborhood                                                  
Arverne                            2              40.589144   
Astoria                            1              40.768509   
Astoria Heights                    6              40.770317   
Auburndale                         8              40.761730   
Bay Terrace                        3              40.782843   
Bayside                            3              40.766041   
Beechhurst                         3              40.792781   
Bellaire                           7              40.733014   
Belle Harbor                       9              40.576156   
Bellerose                          4              40.728573   
Blissville                         7              40.737251   
Briarwood                          6              40.710935   
Broad Channel                      2              40.603027   
Brookville                         5              40.660003   
Cambria Heights                    4              40.692775   
College Point                      8              40.784903   
Corona                             8              40.742382   
Douglaston                         1              40.766846   
East Elmhurst                      8              40.764073   
Edgemere                           2              40.595642   
Elmhurst                           3              40.744049   
Far Rockaway                       2              40.603134   
Floral Park                        4              40.741378   
Flushing                           0              40.764454   
Forest Hills                       3              40.725264   
Forest Hills Gardens               3              40.714611   
Fresh Meadows                      3              40.734394   
Glen Oaks                          4              40.749441   
Glendale                           1              40.702762   
Hammels                            2              40.587338   
Hillcrest                          3              40.723825   
Hollis                             1              40.711243   
Holliswood                         1              40.720957   
Howard Beach                       5              40.654225   
Hunters Point                      4              40.743414   
Jackson Heights                    3              40.751981   
Jamaica Center                     6              40.704657   
Jamaica Estates                    6              40.716805   
Jamaica Hills                      6              40.711460   
Kew Gardens                        6              40.705179   
Kew Gardens Hills                  3              40.722578   
Laurelton                          5              40.667884   
Lefrak City                        3              40.736075   
Lindenwood                         4              40.663918   
Little Neck                        1              40.770826   
Long Island City                   7              40.750217   
Malba                              8              40.790602   
Maspeth                            6              40.725427   
Middle Village                     6              40.716415   
Murray Hill                        0              40.764126   
North Corona                       8              40.754071   
Oakland Gardens                    6              40.745619   
Ozone Park                         7              40.680708   
Pomonok                            8              40.734936   
Queens Village                     7              40.718893   
Queensboro Hill                    0              40.744572   
Queensbridge                       7              40.756091   
Ravenswood                         7              40.761705   
Rego Park                          3              40.728974   
Richmond Hill                      6              40.697947   
Ridgewood                          1              40.708323   
Rochdale                           4              40.

In [125]:
# create map
from folium.features import DivIcon
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Q_distance_M['Neighborhood Latitude'], Q_distance_M['Neighborhood Longitude'], Q_distance_M.index, Q_distance_M['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
    folium.Marker([lat, lon], icon = DivIcon(icon_size=(150,36),
        icon_anchor=(0,0),
        html=f"""<div style="font-family: courier new; color: black ">{"{:.0f}".format(cluster)}</div>""",
        )).add_to(map_clusters)
       
map_clusters

In [102]:
Q_merge = Q_mergeD.drop(columns=['Distance'], axis = 1)

In [103]:
Y = Q_merge.values[:,1:]
clus_KdataY = StandardScaler().fit_transform(Y)
k_means = KMeans(init = "k-means++", n_clusters = kclusters, n_init = 100)
k_means.fit(clus_KdataY)
K_labelsY = k_means.labels_
K_labelsY

array([3, 8, 3, 3, 3, 3, 2, 3, 2, 2, 2, 2, 3, 2, 0, 3, 3, 2, 3, 0, 5, 0,
       2, 6, 3, 3, 2, 3, 2, 0, 3, 0, 0, 3, 3, 3, 3, 2, 0, 3, 3, 0, 3, 2,
       2, 3, 2, 3, 2, 3, 2, 7, 3, 3, 0, 3, 2, 3, 3, 0, 1, 0, 4, 3, 0, 2,
       2, 2, 0, 0, 3, 3, 9, 2, 2, 2, 3], dtype=int32)

In [104]:
Q_distance_M.insert(0, 'Cluster Labels woD', K_labelsY)
Q_distance_M

Cluster Labels woD  Cluster Labels  \
Neighborhood                                               
Arverne                                3               2   
Astoria                                8               1   
Astoria Heights                        3               6   
Auburndale                             3               8   
Bay Terrace                            3               3   
Bayside                                3               3   
Beechhurst                             2               3   
Bellaire                               3               7   
Belle Harbor                           2               9   
Bellerose                              2               4   
Blissville                             2               7   
Briarwood                              2               6   
Broad Channel                          3               2   
Brookville                             2               5   
Cambria Heights                        0               4   
College Point                          3               8   
Corona                                 3               8   
Douglaston                             2               1   
East Elmhurst                          3               8   
Edgemere                               0               2   
Elmhurst                               5               3   
Far Rockaway                           0               2   
Floral Park                            2               4   
Flushing                               6               0   
Forest Hills                           3               3   
Forest Hills Gardens                   3               3   
Fresh Meadows                          2               3   
Glen Oaks                              3               4   
Glendale                               2               1   
Hammels                                0               2   
Hillcrest                              3               3   
Hollis                                 0               1   
Holliswood                             0               1   
Howard Beach                           3               5   
Hunters Point                          3               4   
Jackson Heights                        3               3   
Jamaica Center                         3               6   
Jamaica Estates                        2               6   
Jamaica Hills                          0               6   
Kew Gardens                            3               6   
Kew Gardens Hills                      3               3   
Laurelton                              0               5   
Lefrak City                            3               3   
Lindenwood                             2               4   
Little Neck                            2               1   
Long Island City                       3               7   
Malba                                  2               8   
Maspeth                                3               6   
Middle Village                         2               6   
Murray Hill                            3               0   
North Corona                           2               8   
Oakland Gardens                        7               6   
Ozone Park                             3               7   
Pomonok                                3               8   
Queens Village                         0               7   
Queensboro Hill                        3               0   
Queensbridge                           2               7   
Ravenswood                             3               7   
Rego Park                              3               3   
Richmond Hill                          0               6   
Ridgewood                              1               1   
Rochdale                               0               4   
Rockaway Beach                         4               2   
Rockaway Park                          3               9   
Rosedale                               0               5   
Ro

In [124]:
# create map
map_clustersY = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Q_distance_M['Neighborhood Latitude'], Q_distance_M['Neighborhood Longitude'], Q_distance_M.index, Q_distance_M['Cluster Labels woD']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersY)
    folium.Marker([lat, lon], icon = DivIcon(icon_size=(150,36),
        icon_anchor=(0,0),
        html=f"""<div style="font-family: courier new; color: black ">{"{:.0f}".format(cluster)}</div>""",
        )).add_to(map_clustersY)
       
map_clustersY

In [107]:
Q_mergeD.insert(0, 'Cluster Labels Distance', K_labels)

In [108]:
Q_mergeD.insert(0, 'Cluster Labels woD', K_labelsY)

In [110]:
Q_MD = Q_mergeD.set_index('Neighborhood')

### Group the neighborhood by cluster labels with distance parameter

In [114]:
Q_mergeD.groupby(['Cluster Labels Distance', 'Neighborhood']).mean()

Cluster Labels woD  \
Cluster Labels Distance Neighborhood                               
0                       Flushing                               6   
                        Murray Hill                            3   
                        Queensboro Hill                        3   
1                       Astoria                                8   
                        Douglaston                             2   
                        Glendale                               2   
                        Hollis                                 0   
                        Holliswood                             0   
                        Little Neck                            2   
                        Ridgewood                              1   
                        South Jamaica                          2   
                        Sunnyside                              3   
                        Sunnyside Gardens                      9   
                        Woodhaven                              2   
2                       Arverne                                3   
                        Broad Channel                          3   
                        Edgemere                               0   
                        Far Rockaway                           0   
                        Hammels                                0   
                        Rockaway Beach                         4   
3                       Bay Terrace                            3   
                        Bayside                                3   
                        Beechhurst                             2   
                        Elmhurst                               5   
                        Forest Hills                           3   
                        Forest Hills Gardens                   3   
                        Fresh Meadows                          2   
                        Hillcrest                              3   
                        Jackson Heights                        3   
                        Kew Gardens Hills                      3   
                        Lefrak City                            3   
                        Rego Park                              3   
                        Utopia                                 2   
4                       Bellerose                              2   
                        Cambria Heights                        0   
                        Floral Park                            2   
                        Glen Oaks                              3   
                        Hunters Point                          3   
                        Lindenwood                             2   
                        Rochdale                               0   
                        South Ozone Park                       2   
5                       Brookville                             2   
                        Howard Beach                           3   
                        Laurelton                              0   
                        Rosedale                               0   
                        Springfield Gardens                    0   
6                       Astoria Heights                        3   
                        Briarwood                              2   
                        Jamaica Center                         3   
                        Jamaica Estates                        2   
                        Jamaica Hills                          0   
                        Kew Gardens                            3   
                        Maspeth                                3   
                        Middle Village                         2   
                        Oakland Gardens                        7   
                        Richmond Hill                          0   
                        Steinway                               3   
                        Woodside  

### Group the neighborhood by cluster labels w/o distance
This table represents that we can get the shop information of each cluster. With the zero value in a cluster, we can know there are no such categories restaurant or food shop in that cluster or area, so it means there are no competitor in this cluster. 

In [116]:
Q_mergeD.groupby(['Cluster Labels woD']).mean()

Cluster Labels Distance  Afghan Restaurant  \
Cluster Labels woD                                               
0                                  4.071429           0.003759   
1                                  1.000000           0.000000   
2                                  4.739130           0.003953   
3                                  4.787879           0.000797   
4                                  2.000000           0.000000   
5                                  3.000000           0.000000   
6                                  0.000000           0.000000   
7                                  6.000000           0.000000   
8                                  1.000000           0.000000   
9                                  1.000000           0.000000   

                    American Restaurant  Arepa Restaurant  \
Cluster Labels woD                                          
0                              0.000000          0.000000   
1                              0.000000          0.000000   
2                              0.002717          0.002070   
3                              0.026055          0.000439   
4                              0.000000          0.066667   
5                              0.000000          0.000000   
6                              0.000000          0.000000   
7                              0.000000          0.000000   
8                              0.011236          0.000000   
9                              0.050633          0.000000   

                    Argentinian Restaurant  Asian Restaurant  BBQ Joint  \
Cluster Labels woD                                                        
0                                 0.000000          0.039708   0.000000   
1                                 0.000000          0.023810   0.000000   
2                                 0.000000          0.000000   0.000000   
3                                 0.000497          0.014690   0.004676   
4                                 0.000000          0.000000   0.066667   
5                                 0.040000          0.000000   0.000000   
6                                 0.000000          0.044776   0.029851   
7                                 0.000000          0.000000   0.000000   
8                                 0.000000          0.000000   0.011236   
9                                 0.000000          0.025316   0.000000   

                    Bagel Shop    Bakery    Bistro  Brazilian Restaurant  \
Cluster Labels woD                                                         
0                     0.000000  0.046220  0.000000              0.000000   
1                     0.000000  0.071429  0.000000              0.000000   
2                     0.016201  0.051295  0.000000              0.000000   
3                     0.023654  0.049061  0.001957              0.000797   
4                     0.066667  0.000000  0.000000              0.033333   
5                     0.000000  0.000000  0.000000              0.000000   
6                     0.000000  0.089552  0.000000              0.000000   
7                     0.035714  0.035714  0.000000              0.000000   
8                     0.022472  0.067416  0.000000              0.011236   
9                     0.000000  0.075949  0.012658              0.000000   

                    Breakfast Spot    Buffet  Burger Joint  Burrito Place  \
Cluster Labels woD                                                          
0                         0.015558  0.000000      0.000000       0.000000   
1                         0.000000  0.000000      0.000000       0.000000   
2                         0.000000  0.000000      0.000000       0.002899   
3                         0.010239  0.001305      0.012668       0.004461   
4                         0.033333  0.000000      0.000000       0.033333   
5                         0.000000  0.000000      0.000000       0.000000   
6                         0.000000  0.000000      0.000000      

### Results and Discussion
With K-means clustering, we can get two clustering results. First one is clustering by distance, it represents the traffic convinence. The second one is clustering by catergories of restaurant or food shop. With these two information, everyone who want to open a restaurant or food shop can determine what kind of restaurant they could open better and which location is better for traffic convinence or more crowd. <br>
For example, if someone want to open a Korean restaurant, he can choose 0, 4, 5 clusters from the table grouped by labels without distance data. In these cluster, there is no Korean restaurant competitor. Then, in the 0 and some 5 cluster, the distance to Flushing Main Street is similar, so he can choose one of these neighborhood to open his restaurant.

### Conclusion
Using the Geojson data and Foursquare API, we can get the venue categories and distance information, and with the clustering algorithm in Python, we can get similar kind of restaurant categories or distance in each cluster. According to which kind of restaurant or food shop someone want to open, we can use the table grouped by cluster labels with categories to find which cluster has no similar category competitor. Then using the cluster grouped by distance, we can choose the closest neighborhood. With analysis method in this project, we can determine which neighborhood is propriate to open a new restaurant or food shop.